# Wikipedia Analysis: PageRank algorithm

Lucía Cordero Sánchez and Lucía León Marco  
100451778 and 100451897

First, import the necessary libraries.

In [ ]:
import pandas as pd
import re
import math as m

In [ ]:
from pyspark.sql.types import *
from pyspark.sql.types import ArrayType, StringType,LongType
from pyspark.sql import functions as F

# What is PageRank?
The PageRank algorithm outputs a probability distribution used to represent the likelihood that a person randomly clicking on links will arrive at any particular page. 
PageRank requires several iterations through the collection of data to adjust the values to reflect the theoretical true value more accurately.

# How to implement Page Rank?

1. Check the structure of the initial data
2. Extract each page's ID and its list of links
3. Transform *List of links* to *Forward Links* so, for example, if A has a list of 8 links, after applying the renaming A's list of links will contain the ID of the links.
4. Compute the number of output links.
5. Create a *Reverse Links Table*
6. Initialize the algorithm
7. Steps 1-6 until one of the following is fulfilled: convergence, or reaches the number of iterations.

In [ ]:
spark.conf.set("spark.sql.execution.arrow.enabled", "true")

# 1. Check the structure of the initial data

In [ ]:
wikipediaDF=spark.read.parquet("dbfs:/databricks-datasets/wikipedia-datasets/data-001/en_wikipedia/articles-only-parquet") # We define the whole Wikipedia database

In [ ]:
wikipediaDF.count() # This would be the total pages that we can work with

Out[5]: 5823210

In [ ]:
PartialWikipediaDF=wikipediaDF.sample(fraction=0.0001,seed=0).cache() # Here we declare a variable with the 0,01% of the database to make it feasible to compute with our computer

In [ ]:
PartialWikipediaDF.count() # This would be number the pages that we are going to use

Out[7]: 576

In [ ]:
display(PartialWikipediaDF) # check the observations 

title id revisionId revisionTimestamp revisionUsername revisionUsernameId text Godzilla 11986 683608938 2015-10-01T10:45:31.000+0000 Mariomassone 8097292 {{About|the monster|the film franchise|Godzilla (franchise)|other uses}} {{redirect|ゴジラ|other uses of "Gojira"|Gojira (disambiguation)}} {{pp-move-indef|small=yes}}{{pp-semi-indef|small=yes}} <!-- This article was pared-down and heavily rewritten because it was a bloated with unsourced information and written in an inappropriate in-universe tone. Brevity is the soul of wit, please do not copy/paste information from Wikizilla or remove citations. --> {{Infobox character | colour = #001 | colour text = #ffa | name = Godzilla | series = [[Godzilla (franchise)|Godzilla film series]] | image = Godzilla '54 design.jpg | image_size = 320px | alt = | caption = Godzilla featured in the [[Godzilla (1954 film)|original film]] | first = ''[[Godzilla (1954 film)|Godzilla]]'' (1954) | last = ''[[Godzilla (2014 film)|Godzilla]]'' (2014) | creator = {{Plainlist| * [[Tomoyuki Tanaka]] * [[Ishirō Honda]] * [[Eiji Tsubaraya]] }} | portrayer = {{Plainlist| * '''Shōwa series''': * [[Haruo Nakajima]] {{cite video|people=[[Takeo Murata]] (writer) and [[Ishirō Honda]] (writer/director)|title=''[[Godzilla (1954 film)|Godzilla]]''|medium=[[DVD]]|publisher=[[Classic Media]]|date=2006}} {{cite video|people=[[Al C. Ward]] (writer) and [[Ishirō Honda]], [[Terry Morse]] (writers/directors)|title=''[[Godzilla, King of the Monsters!]]''|medium=[[DVD]]|publisher=[[Classic Media]]|date=2006}} * [[Katsumi Tezuka]] * [[Yū Sekida]] * Ryosaku Takasugi * [[Seiji Onaka]] * Shinji Takagi * Isao Zushi * [[Toru Kawai]] * '''Heisei series''': * [[Kenpachiro Satsuma]] * '''Millennium series''': * [[Tsutomu Kitagawa]] * [[Mizuho Yoshida (actor)|Mizuho Yoshida]] * '''TriStar Pictures''': * Kurt Carley {{cite web|url=http://www.tohokingdom.com/articles/2014-11-07_nakajima_carley_godzilla_1954_1998.html|title=Nakajima and Carley: Godzilla's 1954 and 1998|last=Mirjahangir|first=Chris|work=Toho Kingdom|date=November 7, 2014|accessdate=April 5, 2015}} * '''Legendary Pictures''': * TJ Storm {{cite web|url=http://translate.google.com/translate?hl=en&sl=es&u=http://www.crhoy.com/conozca-al-actor-que-da-vida-a-godzilla-quien-hablo-con-crhoy-com-v2k0k2x/&prev=search|title= Meet the actor who gives life to Godzilla|last=Arce|first=Sergio|work=crhoy.com|date=May 29, 2014|accessdate=March 26, 2015}} }} | lbl1 = Designed by | data1 = {{Plainlist| * [[Akira Watanabe (film art director)|Akira Watanabe]] * [[Teizô Toshimitsu]] Classic Media Godzilla 2006 DVD - [http://www.youtube.com/watch?v=yfSARjZ0OXc Special Features: Making of The Godzilla Suit] - Ed Godziszewski }} | alias = {{Plainlist| * King of the Monsters ''[[Godzilla, King of the Monsters!]]'' (1956). Directed by [[Ishirō Honda]] and [[Terry O. Morse]]. [[Toho]] ''[[Godzilla vs. Megaguirus]]'' (2000). Directed by Masaaki Tezuka. [[Toho]] ''[[Godzilla: Final Wars]]'' (2004). Directed by [[Ryuhei Kitamura]]. [[Toho]] {{cite web |url=http://www.comics.org/series/2392/covers |title=GCD :: Covers :: Godzilla |publisher=Comics.org |accessdate=October 18, 2011}} * Gigantis ''[[Godzilla Raids Again#English version|Godzilla Raids Again]]'' (US release) 1959 [[Toho]] * Monster Zero-One ''[[Invasion of Astro-Monster]]'' (1965). Directed by [[Ishirō Honda]]. [[Toho]] * God of Destruction ''[https://www.youtube.com/watch?v=ohbMHoX2B48 Godzila, Mothra, and King Ghidorah]'' (2001). Directed by [[Shusuke Kaneko]]. [[Toho]] {{cite web |url=http://www.scifijapan.com/articles/2010/07/04/godzilla-perfect-collection-box-6/ |title=GODZILLA SOUNDTRACK PERFECT COLLECTION BOX 6|last=DeSentis|first=John|work=Scifi Japan|accessdate=November 23, 2014}} * Alpha Predator ''[[Godzilla (2014 film)|Godzilla]]'' (2014). Directed by [[Gareth Edwards (director)|Gareth Edwards]]. [[Legendary Pictures]] }} | species = [[Kaiju|Daikaiju]] }} {{nihongo|'''Godzilla'''|ゴジラ|Gojira}} ({{IPAc-en|ɡ|ɒ|d|ˈ|z|ɪ|l|ə}}; {{IPA-ja|

## Useful information about the initial data
* *title*: Title of the page
* *id*: Identificacion number of the page
* *text*: Information in the page.

# 2. Extract each page's ID, text and its list of links

Now we are going to implement the *parse_links* function. As it is not callable from the Spark dataframe we will also define the User Defined Function (udf). 

The *parse_links* function receives a string (text) and returns the list containing the links, once we have filtered from the candidate links.

In [ ]:
# We tried to extract the titles from the WikipediaDF to compare them with the candidate links and discard those ones which are not pages of Wikipedia but it was unfeasible due to its size. 
#wikipediaDF=wikipediaDF.toPandas()
#title_list=wikipediaDF['title'].tolist()
# title_list

In [ ]:

def parse_links(document_body):
  document_body = document_body.lower() #standarize text to lower case 
  data = re.findall(r'\[\[(.+?)\]\]', document_body) # use regular expressions to find the possible links
  links = [] #  list of links
  if (len(data)>0): # execute it if there is at least one link in the page
    words = ["wikipedia:","video:","category:","wkt:","w:","template:"] 
         
    # for deleting the instances with the previous words: 
    for s in data: # iterate over the candidate links
      for word in words: # iterate over the words that cannot have links
        if word in s: # if that word is in the candidate link
           data[data.index(s)]='none' # set that link to 'none'

    # remove all the 'none' instances from the database
    while 'none' in data: 
      data.remove('none')
        
    for s in data: # iterate over the candidate links in the data list
      
      # For format [[file: [[link]] ]] 
      if "file:" in s:
        links.append(s.split("[[")[-1])

      # For format [[image: [[link]] ]] 
      if "image:" in s:
        links.append(s.split("[[")[-1])

      # For format  [[ link1|link2 ]] 
      if "|" in s and "file:" not in s and "image:" not in s:
        links.extend(s.split("|"))

      # For format  [[link]] 
      if "file:" not in s and "image:" not in s and "|" not in s: 
        links.append(s)

    
  return links #return the list of final links

We use the following text to check that the function *parse_links* works.

In [ ]:
test="{{Use Indian English|date=April 2015}} {{Infobox person | name = Shavez Khan | image = | caption = | birth_date = | birth_place = India | nationality = India | residence = [[Mumbai]], India | occupation = [[Actor]] | years_active = present | height = }} '''Shavez Khan''' is an [[India]]n television [[actor]]. He has done his roles in various Indian television shows like Shaitaan,<ref>{{cite web|url=http://www.tellychakkar.com/tv/tv-news/shavez-khan-feature-episodic-of-colors-shaitaan|title=Shavez Khan to feature in an episodic of Colors' Shaitaan|work=Tellychakkar|date=11 April 2013|accessdate=24 April 2015}}</ref> [[Encounter (Indian TV series)|Encounter]], [[Ek Hasina Thi (TV series)|Ek Hasina Thi]], [[Savdhaan India]],<ref>{{cite web|url=http://www.tellychakkar.com/tv/tv-news/shavez-khan-anshul-singh-and-damini-joshi-episodic-of-savdhan-india-140915|title=Shavez Khan, Anshul Singh and Damini Joshi in an episodic of Savdhan India|work=Tellychakkar|date=15 September 2014|accessdate=24 April 2015}}</ref> [[SuperCops vs Supervillains]],<ref>{{cite web|url=http://www.tellychakkar.com/tv/tv-news/rituraj-singh-and-shavez-khan-life-oks-shapath-141009|title=Rituraj Singh and Shavez Khan in Life OK's Shapath|work=Tellychakkar|date=9 October 2014|accessdate=24 April 2015}}</ref> Pyaar Ka The End,<ref>{{cite web|url=http://www.tellychakkar.com/tv/tv-news/shavez-khan-bindass-pyaar-ka-the-end-141029|title=Shavez Khan in Bindass' Pyaar Ka The End|work=Tellychakkar|date=29 October 2014|accessdate=24 April 2015}}</ref> [[Pyaar Kii Ye Ek Kahaani]], [[MTV Fanaah]], [[Crime Patrol (TV series)|Crime Patrol]]. He has played his recent role in [[Sony Entertainment Television (India)|Sony TV]]'s [[C.I.D. (Indian TV series)|CID]].<ref>{{cite web|url=http://www.tellychakkar.com/tv/tv-news/shavez-khan-sony-tvs-cid-150417|title=Shavez Khan in Sony TV's CID|work=Tellychakkar|date=17 April 2015|accessdate=24 April 2015}}</ref> ==Television== *[[Colors (TV channel)|Colors]]'s Shaitaan *[[Sony Entertainment Television (India)|Sony TV]]'s [[Encounter (Indian TV series)|Encounter]], [[Crime Patrol (TV series)|Crime Patrol]] & [[C.I.D. (Indian TV series)|CID]] *[[Star Plus]]'s [[Ek Hasina Thi (TV series)|Ek Hasina Thi]] *[[Life OK]]'s [[Savdhaan India]] & [[SuperCops vs Supervillains]] *[[Bindass]]' Pyaar Ka The End *[[Star One]]'s [[Pyaar Kii Ye Ek Kahaani]] *[[MTV]]'s [[MTV Fanaah]] ==References== {{Reflist}} ==External links== {{Persondata | NAME = Khan, Shavez | ALTERNATIVE NAMES = | SHORT DESCRIPTION = Indian model and television actor | DATE OF BIRTH = <!--Birth date has been contested. Do not add without providing a reliably published source with a reputation for editorial oversight--> | PLACE OF BIRTH = India | DATE OF DEATH = | PLACE OF DEATH = }} {{DEFAULTSORT:Khan, Shavez}} [[Category:Living people]] [[Category:Indian male television actors]] [[Category:Actors in Hindi television]] [[Category:Indian television personalities]]"

In [ ]:
parse_links(test) # We check that it works as it should.

Out[12]: ['mumbai',
 'actor',
 'india',
 'actor',
 'encounter (indian tv series)',
 'encounter',
 'ek hasina thi (tv series)',
 'ek hasina thi',
 'savdhaan india',
 'supercops vs supervillains',
 'pyaar kii ye ek kahaani',
 'mtv fanaah',
 'crime patrol (tv series)',
 'crime patrol',
 'sony entertainment television (india)',
 'sony tv',
 'c.i.d. (indian tv series)',
 'cid',
 'colors (tv channel)',
 'colors',
 'sony entertainment television (india)',
 'sony tv',
 'encounter (indian tv series)',
 'encounter',
 'crime patrol (tv series)',
 'crime patrol',
 'c.i.d. (indian tv series)',
 'cid',
 'star plus',
 'ek hasina thi (tv series)',
 'ek hasina thi',
 'life ok',
 'savdhaan india',
 'supercops vs supervillains',
 'bindass',
 'star one',
 'pyaar kii ye ek kahaani',
 'mtv',
 'mtv fanaah']

Now that we checked that it works, we can apply the function to the corresponding text.

In [ ]:
parse_links_udf = udf(parse_links,ArrayType(StringType())) # apply parse_links function to all the text using a udf

In [ ]:
tolower_udf= udf(lambda x: x.lower()) # used to convert text to lowercase

In [ ]:
TempForwardDF = PartialWikipediaDF.select(tolower_udf("title").alias("title"),"id",parse_links_udf("text").alias("links")) # we create a table with the titles, IDs and links, renaming when needed

In [ ]:
display(TempForwardDF) # display the table 

title id links godzilla 11986 List(godzilla (franchise), godzilla film series, godzilla (1954 film), original film, godzilla (1954 film), godzilla, godzilla (2014 film), godzilla, tomoyuki tanaka, ishirō honda, eiji tsubaraya, haruo nakajima, takeo murata, ishirō honda, godzilla (1954 film), godzilla, dvd, classic media, al c. ward, ishirō honda, terry morse, godzilla, king of the monsters!, dvd, classic media, katsumi tezuka, yū sekida, seiji onaka, toru kawai, kenpachiro satsuma, tsutomu kitagawa, mizuho yoshida (actor), mizuho yoshida, akira watanabe (film art director), akira watanabe, teizô toshimitsu, godzilla, king of the monsters!, ishirō honda, terry o. morse, toho, godzilla vs. megaguirus, toho, godzilla: final wars, ryuhei kitamura, toho, godzilla raids again#english version, godzilla raids again, toho, invasion of astro-monster, ishirō honda, toho, shusuke kaneko, toho, godzilla (2014 film), godzilla, gareth edwards (director), gareth edwards, legendary pictures, kaiju, daikaiju, kaiju, daikaiju, tokusatsu, godzilla (franchise), films of the same name, japan, ishirō honda, godzilla (1954 film), godzilla, godzilla video games, video games, godzilla (comics), comic books, godzilla (franchise)#television, television shows, toho, godzilla_(franchise)#american_films, two hollywood films, godzilla, king of the monsters!, nuclear bombings of hiroshima and nagasaki, daigo fukuryū maru, lucky dragon 5, nuclear weapon, portmanteau, gorilla, whale, ateji, kanji, hepburn romanization, kunrei romanization, godzilla: final wars, ray harryhausen, the beast from 20,000 fathoms, amphibian, amphibious, dinosaur, wired (magazine), wired, tyrannosaurus, iguanodon, stegosaurus, alligator, usa today, chimera (mythology), chimera, life (magazine), ''life'' magazine, keloid, hibakusha, hiroshima's survivors, turner classic movies, akira ifukube, double bass, contrabass, godzilla 2000, godzilla (1954 film)|godzilla, black belt (martial arts), black belt, godzilla raids again, transitional form, regeneration (biology), regenerate, godzilla 2000, takao okawara, toho, godzilla vs. king ghidorah, kazuki ōmori, toho, godzilla vs. mechagodzilla, jun fukuda, toho, godzilla vs. biollante, kazuki ōmori, toho, godzilla: destroy all monsters melee, pipeworks software, zone fighter, the godzilla power hour, godzilla vs. hedorah, yoshimitsu banno, toho, ghidorah, the three-headed monster, ishirō honda, toho, godzilla: unleashed, the return of godzilla, koji hashimoto (director), koji hashimoto, toho, shinto, king kong, king kong vs. godzilla, gender-neutral pronoun, godzilla (1998 film), 1998 godzilla film, parthogenesis, jsdf, king ghidorah, gigan, mechagodzilla, megalon, biollante, megaguirus, mothra, rodan, anguirus, minilla, king kong, fantastic four, godzilla (1954 film), the original 1954 film, godzilla, king of the monsters!, 1956 american version, joseph e. levine, tokyo metropolitan government building, godzilla vs. king ghidorah, legendary pictures, legendary, godzilla (2014 film), godzilla, gareth edwards (director), gareth edwards, godzilla (2016 film), upcoming toho godzilla film, godzilla raids again, suitmation, an actor wearing a latex costume, animatronics, animatronic, stop-motion, computer generated imagery, computer-generated, king kong (1933 film), king kong, eiji tsuburaya, the return of godzilla, godzilla vs biollante, godzilla vs destoroyah, kenpachiro satsuma, oxygen deprivation, godzilla vs. spacegodzilla, patrick tatopoulos, motion capture, digitigrade, computer-generated imagery, cgi, stan winston, jurassic park (film), jurassic park, the moving picture company, bear, komodo dragon, lizard, lion, gray wolf, wolves, the hollywood reporter, hollywood walk of fame, popular culture, kaijū, kaiju, tokusatsu, metaphor, atomic bombings of hiroshima and nagasaki, mtv movie awards#mtv lifetime achievement award, mtv lifetime achievement award, hollywood walk of fame, godzilla: final wars, bambi meets godzilla, mystery science theater

# 3. Create the *Forward Links* table

*Forward Links* table contains the id of each Wikipedia page and the id of the links that are mentioned in that page.

In [ ]:
titleidDF=wikipediaDF.select("id",tolower_udf("title").alias("title")); #select title and id from the wikipedia dataset

In [ ]:
titleidPDF=titleidDF.toPandas() #convert title to pandas

We define a function to convert the titles of the pages to ids

In [ ]:
def title2id(links , title_idxPDF): 
  if ( len(links)>0): # check that the list of links has at least one link
    id_list = title_idxPDF[title_idxPDF.title.isin(links)].id.to_list() # convert each of them to id
  else:
    id_list = [] # if there are no links, the results list will be empty
  return id_list # return the list of results

Broadcast variables allow us to keep a read-only variable cached on each machine rather than shipping a copy of it with tasks.
Here we will use the broadcast as it boosts performance. It is preferable over cache because it is not a lazy evaluation operation and it reduces communication costs of data over the network by providing a copy of shared data to each executor.

In [ ]:
broadcast_title_idPDF = sc.broadcast(titleidPDF)

In [ ]:
def title2id_2(links):
  title_idxPDF = broadcast_title_idPDF.value # use the broadcast values
  if ( len(links)>0): # check that the list of links has at least one link
    id_list = title_idxPDF[title_idxPDF.title.isin(links)].id.to_list() # convert each of them to id
  else:
    id_list = [] # if there are no links, the results list will be empty
  return id_list # return the list of results

We define a variable test_list with a list of links to check that the function works.

In [ ]:
test_list=["shenzhou (spacecraft)|shenzhou", "long march 2f|chang zheng 2f", "jiuquan satellite launch center|jiuquan", "jiuquan launch area 4|la-4/sls-1", "geocentric orbit|geocentric", "low earth orbit|low earth", "yang liwei", "shenzhou 4", "shenzhou 6", "shenzhou program|shenzhou", "human spaceflight", "chinese space program", "shenzhou spacecraft", "long march 2f", "soviet union", "russia", "united states", "file:yang liwei.jpg|thumb|left|[[yang liwei", "yang liwei", "chinese nationalism", "united nations", "people's daily", "spacedaily", "political status of taiwan|taiwan", "people's daily", "general secretary of the communist party of china|general secretary", "president of the people's republic of china|president", "hu jintao", "great hall of the people", "sina.com", "central committee of the communist party of china|cpc central committee", "state council of china|state council", "central military commission", "sina.com", "prime minister of japan|prime minister", "junichiro koizumi", "cctv.com", "george w. bush", "united states department of state|u.s. state department", "sean o'keefe", "dprk", "kwangmyŏngsŏng-1", "yang liwei", "chinese space program", "tiangong program", "shenzhou spacecraft", "long march rocket", "jiuquan satellite launch center", "shenzhou 4", "shenzhou 6", "category:human spaceflights|shenzhou 05", "category:shenzhou program|shenzhou 05", "category:spacecraft launched in 2003", "category:2003 in china"]

In [ ]:
idx_list=title2id(test_list,titleidPDF) 
#idx_list # the function has worked and now the links are ids

Set a user defined function with the *titles2id_2* funuction defined before.

In [ ]:
udf_title2id_2 =udf(title2id_2,ArrayType(LongType()))

Get the final **ForwardDF** from the **TempForwardDF** selecting the id column and the generated links column.

In [ ]:
ForwardDF = TempForwardDF.select("id",udf_title2id_2("links").alias("links")).cache() 

In [ ]:
display(ForwardDF) # display the new table

id links 11986 List(15573, 15655, 621, 3921, 21502, 21785, 33702, 33777, 36865, 36896, 28272, 11664, 11986, 11988, 12000, 12004, 12005, 12546, 13729, 30467, 30683, 4400, 6080, 6231, 7333, 17360, 18184, 20518, 59361, 68485, 37604, 65001, 65411, 187479, 192790, 325852, 325875, 208463, 162143, 79887, 226575, 228798, 147734, 87451, 87929, 248760, 396968, 266204, 267370, 438275, 634965, 567874, 570258, 570263, 570279, 541707, 870601, 894309, 490771, 490777, 854081, 719793, 1356696, 1252253, 1190931, 1222711, 1407410, 925736, 930853, 1112869, 1670693, 1646358, 623256, 1009817, 1922658, 1862287, 1909502, 791422, 1947751, 1236610, 1236650, 1245556, 2348754, 2156483, 105776, 1790878, 3135027, 5220058, 3572981, 4726468, 4259513, 3540339, 2717151, 30863297, 4627056, 30863297, 5765607, 2120494, 9322751, 9073903, 9182702, 9182971, 7396632, 10043508, 11014498, 11056991, 8660880, 11778948, 16823212, 12031833, 31626763, 31626763, 8233, 8311, 15226184, 21123733, 17229419, 37448163, 18057502, 20002271, 37448163, 36101762, 18637733, 18637926, 18652780, 18653283, 18993927, 18998781, 23188764, 30313654, 30313654, 45178603, 19675671, 45178603, 23624578, 302275, 303628, 53430, 54581) 13049 List(15782, 700, 21018, 32742, 32798, 33925, 26202, 12521, 6532, 19444, 43245, 44766, 45777, 47923, 70188, 42368, 199961, 189774, 161275, 323481, 208411, 209892, 213936, 213978, 228998, 230019, 350539, 147635, 153295, 294177, 310113, 86324, 87240, 248859, 383648, 670749, 1047259, 1056621, 94097, 1129578, 946273, 1279006, 1128563, 1550022, 2251504, 875196, 1972169, 2957072, 2427653, 3038250, 2922874, 803804, 5178089, 3745788, 4368178, 2799016, 6148078, 10891114, 7997906, 12785172, 8495660, 1313968, 9258, 21244047, 26255613, 23953851, 36026428, 27480261, 22928212, 36026428, 18622119, 39658852, 39658852, 34115577, 34115577, 34543638, 34543638, 16320493, 32915915, 32915915, 29604227, 29610981) 38010 List(22303, 11024, 13256, 31489, 18957, 44905, 49838, 38481, 200033, 291242, 294126, 85403, 459471, 460321, 5358908, 7372916, 19334830, 9955, 23868856, 42480973, 30206738, 18209535, 43638795, 30206738, 43638795, 18994087, 3117601) 38252 List(15613, 16579, 2028, 2827, 20836, 21001, 21113, 21231, 21233, 22068, 22113, 22308, 23324, 32927, 25180, 25185, 25683, 28309, 28480, 10277, 10510, 12799, 29511, 29812, 30456, 31365, 31453, 32009, 4477, 5166, 6974, 7668, 17292, 19862, 20405, 44635, 44986, 48147, 51503, 51763, 52581, 53207, 57858, 66730, 66919, 70118, 72758, 41523, 42010, 42634, 43008, 65411, 196790, 198217, 202652, 186444, 191086, 155482, 156547, 156699, 156702, 156999, 319442, 205078, 205105, 205126, 167409, 273476, 273484, 273486, 273487, 273489, 276919, 77179, 79026, 81213, 228538, 231297, 232142, 235879, 346978, 148113, 152171, 292778, 310005, 82375, 87731, 87929, 255114, 259082, 423161, 431685, 431695, 238424, 238521, 238715, 407832, 371350, 355118, 170771, 170772, 170773, 170874, 171195, 172350, 174650, 437949, 639185, 416688, 418975, 180103, 182462, 140624, 140630, 146595, 587003, 591556, 555505, 511253, 733668, 681239, 683972, 486312, 491664, 1040371, 1043024, 1102458, 1102461, 719715, 730350, 1072228, 954140, 1351636, 604137, 612293, 92374, 1560005, 1571314, 1574616, 1170208, 1029495, 1407696, 1588483, 1712034, 1714150, 1717489, 1721523, 928738, 947766, 1121666, 1654648, 1926730, 1529230, 1775761, 1732421, 2240220, 797714, 1959430, 2186651, 2291656, 1462102, 2530527, 2555445, 2004720, 2011729, 2011948, 2019694, 1988033, 2000410, 2465857, 2416701, 2416795, 2632114, 2433599, 2041117, 1811772, 2943008, 799436, 805870, 818042, 2520013, 3823213, 3852997, 4166365, 3752874, 2798927, 2808829, 4883556, 4865481, 5126908, 30866008, 5369534, 7038301, 6062032, 30860202, 30866008, 7129894, 136566, 6126173, 5820423, 8953740, 5079506, 7444902, 18933360, 18949200, 8325880, 9282173, 8803981, 6766412, 2776113, 19344515, 19344654, 8642505, 11690592, 11972546, 25804468, 25817785, 17339824, 9510, 9822, 21611071, 12610483, 24047593, 24061144, 915566, 921071, 28178906, 17586829, 3948301

# 4. Compute the number of output links.

In this step, using the **ForwardDF**, our goal is to get the number of links of one page that are pointing to another one (number of output links). Collect the information in a Pandas Dataframe.

In [ ]:
count_linksDF=ForwardDF.select("id",F.size("links").alias("count")) # instead of defining a function using size we reduce the time of execution

In [ ]:
display(count_linksDF)

id count 11986 139 13049 82 38010 27 38252 277 196900 26 201227 39 324799 20 162369 16 340927 31 343031 59 445892 97 520457 16 595343 70 769734 39 126003 30 691955 16 1099529 8 729744 72 95200 29 95544 75 1260076 5 1208418 24 1622517 6 1493498 10 1587990 46 1700608 74 1413986 28 1435291 18 1290489 20 1128231 84 1692269 9 1656558 2 1853709 24 1894904 7 2883053 4 1759378 21 2316601 51 2531861 1 2542615 11 2546735 1 2569366 13 3010702 33 2085757 7 2463328 15 2478982 1 2838121 16 2346009 27 2951463 34 2952555 1 2968866 30 2391890 9 2400112 131 2412019 56 2635587 34 2636494 5 1829185 11 1339199 73 3092841 26 2441191 12 2927619 2 2944487 7 2353318 26 3164637 54 3297267 34 3245646 19 3547454 20 3959881 38 4279399 1 4299833 5 3819676 0 3459701 23 3877002 31 4426000 38 4428471 21 4740986 76 3343252 5 4254040 4 4079737 27 4095359 22 2828195 33 3509649 25 4933184 19 4839391 15 5129755 7 3686661 51 30874030 18 3418750 70 4060126 25 6999804 26 7009414 10 5441158 73 4593460 2 7062711 8 5526067 38 6068800 117 6072667 2 5753223 13 5765638 40 5767425 14 7130222 25 7159975 6 6667872 1 6154286 14 127028 52 129494 26 131337 23 133063 20 10919930 8 10933655 14 6810130 12 6817345 34 7303896 21 7350231 17 8601802 6 113360 61 5477828 7 5922519 22 5789628 20 8755776 6 7543697 21 7714319 9 9314280 10 9345295 17 8015512 3 6570161 15 6572839 4 18952729 33 6231369 10 8971509 1 9597841 81 9143124 13 6379698 13 6411327 17 7956879 39 7413426 9 10686531 2 8565820 8 8779669 2 8807583 2 9630429 11 7930852 10 10524337 16 6913118 71 10755293 32 10771081 59 8179790 13 12737657 7 11274309 25 11321812 9 11050727 50 11063430 7 11807881 2 8660143 24 6264607 17 20895542 52 20923467 23 18733138 5 25837762 6 39350392 12 39378163 108 39384287 8 13400372 80 12513816 8 12545464 28 17517914 7 25702017 14 11011782 28 12870374 2 19369910 22 17358792 6 13403258 43 21630814 12 15062766 9 24018808 13 35789576 49 35827804 26 22371574 18 22410581 28 40787558 4 26463291 9 24678739 8 43821244 4 41011186 6 35817941 6 28144965 3 39467189 5 18572111 19 18847592 9 39225211 6 39249641 5 20084310 14 20084588 10 30268340 9 15419898 6 20482878 17 31461689 15 44338352 22 19728408 8 19754555 13 30717706 26 26036541 39 42677068 7 44375455 7 39273352 14 37957819 11 36281651 4 27330945 6 21435728 128 36995848 15 23879687 25 23880519 5 39416189 2 39447529 9 42305636 10 42343306 12 42358235 13 15415422 7 21144046 3 33699316 13 42460625 14 27954013 3 26616827 1 26746787 10 39440134 12 40864153 12 28087272 12 32101236 42 32141949 10 38167591 6 28893279 23 28903950 8 28925021 5 31550770 8 25428784 2 42671411 12 40573523 13 17956553 10 23638991 6 40966784 3 18294251 13 37242525 2 28379807 8 35637723 2 25336435 21 25383048 5 41329451 18 21823345 3 42258953 6 15790331 7 15822014 5 35667802 11 35691308 16 24082172 23 27374524 2 40085429 60 32113040 0 36304983 10 36309790 13 44331934 12 13511010 9 25964797 20 36881992 5 36893675 46 39882902 19 23504748 10 26869023 39 26893642 8 39071757 9 42447661 1 35953725 15 28311213 15 36034468 9 36082190 14 37987159 6 34035028 14 34111854 24 22359225 21 25020074 1 45410167 17 41984964 12 20645848 20 35507975 7 35538682 19 27456939 30 22911639 15 23736968 67 23743943 25 14758442 7 36828502 3 24808272 15 40066583 3 44931988 48 34283731 16 39852324 18 36489847 2 18874106 15 18900597 12 21552149 20 37050820 11 37071804 10 37076268 3 39014312 25 24908070 11 21795041 12 19956455 17 26655130 11 36135905 8 36162708 9 36163293 5 28206022 10 28243509 6 36338110 36 45427226 6 45446916 6 40643716 21 43089170 2 43095106 12 43101464 5 14451095 11 44687395 9 38784386 8 38798568 20 35482431 16 35518353 10 37752338 62 42806379 14 31194204 10 37054581 0 47779920 9 44519272 17 16650921 5 16656289 28 43674025 8 26516435 29 26523666 9 28867382 7 33994086 10 33999626 5 46998862 8 36407461 15 29498949 51 29569256 9 47009418 9 25552093 10 40729795 6 40752010 65 31352781 31 42876958 19 41124364 15 31060132 4 41631893 13 45290606 12 35741456 16 44051049 27 15569220 5 15572526 5 22187476 7 2222

In [ ]:
count_linksPDF=count_linksDF.toPandas()

# 5. Create a *Reverse Links Table*

The next step is to transform the **ForwardDF** to a reverse table of links.

In [ ]:
def reverseId(id,links):
  if (len(links)>0): # check that there is at least one link in the least
    reverse = [ (tgt_id,id) for tgt_id in links ] # reverse the format
  else:
    reverse=[] # if there are not links, the id_list list still empty
  return reverse # return the id_list

In [ ]:
ForwardRDD = ForwardDF.rdd

In [ ]:
ReverseRDD=( ForwardRDD
            .flatMap(lambda r: reverseId(r.id,r.links))
            .groupByKey()
            .map(lambda r: (r[0],list(r[1])))
            )

In [ ]:
ReverseDF=spark.createDataFrame(ReverseRDD,["id","links"]) # create a spark dataframe with the reverseRDD and the columns id and links

In [ ]:
display(ReverseDF)# display the dataframe

id links 266204 List(11986) 925736 List(11986) 155550 List(445892) 277672 List(445892) 27116818 List(595343) 56120 List(126003, 95544, 127028, 129494, 133063, 11274309) 2526498 List(1700608) 8418 List(2316601, 5441158, 23879687) 152256 List(2463328) 7930 List(2400112, 2828195) 305976 List(2400112) 14120158 List(2412019) 5314808 List(1339199) 65880 List(3164637) 679052 List(2828195) 116022 List(4933184) 35502 List(4060126, 6068800, 10755293, 12545464, 47295933) 4635146 List(5526067) 1452898 List(6068800) 3782000 List(5765638) 895968 List(113360) 404186 List(9143124) 52826 List(8565820) 947696 List(9630429) 22936 List(6913118, 19917252, 45041066, 21884939, 21885285, 33572177) 6466 List(10771081, 41237021) 57706 List(10771081, 27021283) 65758 List(11050727) 39412100 List(39378163, 39378163) 31232 List(13400372) 2319464 List(13400372) 732244 List(12545464) 16277728 List(35789576) 447008 List(22410581) 427976 List(42677068) 200446 List(21435728) 171166 List(33699316, 20669867) 99430 List(28087272, 27208465) 178364 List(31550770) 2347646 List(28379807, 28410278) 363804 List(42258953) 14494576 List(35691308) 8093724 List(40085429) 47489232 List(26869023, 26869023, 37752338, 37752338, 33455832, 33455832) 29432500 List(23736968) 38508080 List(23736968, 23736968) 37300890 List(44931988) 31321182 List(39852324, 39852324) 19870750 List(18900597) 8916248 List(39014312) 237168 List(37752338) 292800 List(40752010) 346358 List(31352781) 32378800 List(37264362, 37264362) 24630214 List(47295933) 47946 List(47492738, 42710337) 45529058 List(45530027, 45530027) 536678 List(46971960) 315858 List(42710337) 564006 List(42710337) 2165866 List(33568964) 22393832 List(33455832) 400892 List(46900222) 1571482 List(41853419) 6799304 List(32004897) 219112 List(33441934) 99308 List(35334900) 372466 List(47670453) 3639017 List(445892) 11123595 List(729744) 17599355 List(95544, 129494, 131337, 133063, 35708021) 1218903 List(1700608) 254127 List(2838121) 838629 List(2951463) 19008577 List(2951463) 5247 List(2391890, 19956455, 32614702) 1059205 List(4426000) 75275 List(2828195) 5040309 List(4933184) 194347 List(3418750) 297071 List(3418750) 3418807 List(3418750) 27995707 List(113360) 2339717 List(6572839) 27283349 List(6572839) 55633 List(9597841, 15790331, 25552093, 23811481, 28466441) 12764007 List(10755293) 1071161 List(10771081) 38261031 List(20895542, 20895542) 21107953 List(20923467) 39614987 List(39378163, 39378163) 3228365 List(24018808) 1171445 List(21435728) 22133851 List(21435728) 5735 List(32101236, 18294251) 25352943 List(42258953) 29830709 List(36893675, 36893675) 3017183 List(23504748) 172997 List(26893642) 11124449 List(28311213) 107361 List(23736968) 22699565 List(36489847) 18456527 List(43089170) 467627 List(35482431) 84303 List(35518353) 31140501 List(35518353, 35518353) 12137537 List(44519272) 90525 List(15572526) 358925 List(36217461) 1078115 List(36217461) 5955309 List(35735414) 345505 List(37264362) 1338951 List(37264362) 592311 List(22457319) 440055 List(23993559) 2111211 List(45041066) 502519 List(23093525) 22205 List(45318426) 82595 List(45318426) 60635 List(13117075) 47192285 List(41836403, 41836403) 34900419 List(45376153, 45376153) 61489 List(33441934) 45001409 List(46226591, 46226591) 10656945 List(47548217) 981125 List(29733373) 19859405 List(34879643) 25913533 List(32281941) 23805739 List(31941257) 446887 List(29960794) 32207879 List(28608194) 248760 List(11986) 105776 List(11986) 2943008 List(38252) 27424748 List(38252) 765430 List(201227, 23993559) 28916 List(445892) 101628 List(445892) 5316396 List(595343) 1099588 List(1099529) 316348 List(1208418) 893408 List(1587990) 1561236 List(1700608) 3988792 List(1700608) 50510 List(2316601) 9640 List(2316601) 28292412 List(2316601) 14194092 List(3010702) 519600 List(2463328) 143230 List(2400112) 8520848 List(2412019) 14119062 List(2412019) 14722840 List(2412019) 26997138 List(1829185, 10771081) 288166 List(3959881) 87110 List(4839391) 294510 List(5441158) 435298 List(5441158) 31600 Lis

# 6. Initialize the algorithm

Now it's time of defining a pandas dataframe with the ids of documents in the previous dataframe (**ReverseDF**).

In [ ]:
damping_factor = 0.85              # probability of a user that stops searching although is not an ending node
max_iterations = 20               # Maximum number of iterations until the algorithm is declares unstable
threshold = 0.0000001              # defines if the difference between the value calculated in the previous iteration is enough bigger to be consider unstable
N = ReverseDF.count()              # The number of documents that we have

In [ ]:
data = list()
for index in ReverseDF.collect():
  data.append(index["id"])                         
PageRankPDF = pd.DataFrame(data,columns=["id"])    # create a pandas dataframe the ids column and the rank of each one

In [ ]:
PageRankPDF["rank"] = damping_factor/N # create the column rank


In [ ]:
display(PageRankPDF) # display page rank pandas dataframe

id rank 266204 9.593679458239277E-5 925736 9.593679458239277E-5 155550 9.593679458239277E-5 277672 9.593679458239277E-5 27116818 9.593679458239277E-5 56120 9.593679458239277E-5 2526498 9.593679458239277E-5 8418 9.593679458239277E-5 152256 9.593679458239277E-5 7930 9.593679458239277E-5 305976 9.593679458239277E-5 14120158 9.593679458239277E-5 5314808 9.593679458239277E-5 65880 9.593679458239277E-5 679052 9.593679458239277E-5 116022 9.593679458239277E-5 35502 9.593679458239277E-5 4635146 9.593679458239277E-5 1452898 9.593679458239277E-5 3782000 9.593679458239277E-5 895968 9.593679458239277E-5 404186 9.593679458239277E-5 52826 9.593679458239277E-5 947696 9.593679458239277E-5 22936 9.593679458239277E-5 6466 9.593679458239277E-5 57706 9.593679458239277E-5 65758 9.593679458239277E-5 39412100 9.593679458239277E-5 31232 9.593679458239277E-5 2319464 9.593679458239277E-5 732244 9.593679458239277E-5 16277728 9.593679458239277E-5 447008 9.593679458239277E-5 427976 9.593679458239277E-5 200446 9.593679458239277E-5 171166 9.593679458239277E-5 99430 9.593679458239277E-5 178364 9.593679458239277E-5 2347646 9.593679458239277E-5 363804 9.593679458239277E-5 14494576 9.593679458239277E-5 8093724 9.593679458239277E-5 47489232 9.593679458239277E-5 29432500 9.593679458239277E-5 38508080 9.593679458239277E-5 37300890 9.593679458239277E-5 31321182 9.593679458239277E-5 19870750 9.593679458239277E-5 8916248 9.593679458239277E-5 237168 9.593679458239277E-5 292800 9.593679458239277E-5 346358 9.593679458239277E-5 32378800 9.593679458239277E-5 24630214 9.593679458239277E-5 47946 9.593679458239277E-5 45529058 9.593679458239277E-5 536678 9.593679458239277E-5 315858 9.593679458239277E-5 564006 9.593679458239277E-5 2165866 9.593679458239277E-5 22393832 9.593679458239277E-5 400892 9.593679458239277E-5 1571482 9.593679458239277E-5 6799304 9.593679458239277E-5 219112 9.593679458239277E-5 99308 9.593679458239277E-5 372466 9.593679458239277E-5 3639017 9.593679458239277E-5 11123595 9.593679458239277E-5 17599355 9.593679458239277E-5 1218903 9.593679458239277E-5 254127 9.593679458239277E-5 838629 9.593679458239277E-5 19008577 9.593679458239277E-5 5247 9.593679458239277E-5 1059205 9.593679458239277E-5 75275 9.593679458239277E-5 5040309 9.593679458239277E-5 194347 9.593679458239277E-5 297071 9.593679458239277E-5 3418807 9.593679458239277E-5 27995707 9.593679458239277E-5 2339717 9.593679458239277E-5 27283349 9.593679458239277E-5 55633 9.593679458239277E-5 12764007 9.593679458239277E-5 1071161 9.593679458239277E-5 38261031 9.593679458239277E-5 21107953 9.593679458239277E-5 39614987 9.593679458239277E-5 3228365 9.593679458239277E-5 1171445 9.593679458239277E-5 22133851 9.593679458239277E-5 5735 9.593679458239277E-5 25352943 9.593679458239277E-5 29830709 9.593679458239277E-5 3017183 9.593679458239277E-5 172997 9.593679458239277E-5 11124449 9.593679458239277E-5 107361 9.593679458239277E-5 22699565 9.593679458239277E-5 18456527 9.593679458239277E-5 467627 9.593679458239277E-5 84303 9.593679458239277E-5 31140501 9.593679458239277E-5 12137537 9.593679458239277E-5 90525 9.593679458239277E-5 358925 9.593679458239277E-5 1078115 9.593679458239277E-5 5955309 9.593679458239277E-5 345505 9.593679458239277E-5 1338951 9.593679458239277E-5 592311 9.593679458239277E-5 440055 9.593679458239277E-5 2111211 9.593679458239277E-5 502519 9.593679458239277E-5 22205 9.593679458239277E-5 82595 9.593679458239277E-5 60635 9.593679458239277E-5 47192285 9.593679458239277E-5 34900419 9.593679458239277E-5 61489 9.593679458239277E-5 45001409 9.593679458239277E-5 10656945 9.593679458239277E-5 981125 9.593679458239277E-5 19859405 9.593679458239277E-5 25913533 9.593679458239277E-5 23805739 9.593679458239277E-5 446887 9.593679458239277E-5 32207879 9.593679458239277E-5 248760 9.593679458239277E-5 105776 9.593679458239277E-5 2943008 9.593679458239277E-5 27424748 9.593679458239277E-5 765430 9.593679458239277E-5 28916 9.593679458239277E-5 101628 9.593679458239277E-5 5316396 9.593679458239277E-5 1099588 9.5936794582

# 7. Implementation: Steps 1-6 until convergence or max iterations

Now, we define a loop:
* While the conditions are not fulfilled:
  * Calculate the new page ranks, invoking the PageRank function from the **ReverseDF**, creating a new Dataframe NewPageRankDF with the [id,new_pagerank] info. 
  * Collect the new page ranks and compares it with the previous **PageRankPDF**, checking if the new Page Ranks vary more than a threshold. If not, the exit condition is complied.
  * Update the **PageRankPDF** with the new values,and update the UDF functions.

In [ ]:
broadcast_count_linksPDF = sc.broadcast(count_linksPDF)  # create a broadcast variable to use it in our function

def new_pagerank(list_of_ids,current_id,current_page_rank): # We receive the parameters
  new_page_rank = 0 # We set the value to 0 for each iteration
  count_links = broadcast_count_linksPDF.value # call to this broadcast table and get the values
  for i in list_of_ids:
    PR = current_page_rank[current_page_rank["id"] == i] # the current value of each of the ids that refer to the corresponding page
    if len(PR)>0: # check if there exist any id in the current_page_rank
      PR = PR.iloc[0][1] 
    else:                                                     
      PR = 0 # if we don’t have this id collected in our current_page_rank, we set it to 0
    count = count_links[count_links["id"] == i] 
    if len(count)>0: # We check if this page has links
      count = count.iloc[0][1] # store this value in count variable
      new_page_rank += PR/count # add PR/count to our new_page_rank that it will the one that we return
      
  new_page_rank = (1-damping_factor)/N + damping_factor*new_page_rank # apply the formula with the damping_factor and N values defined previously
  
  absolute_difference = abs(new_page_rank-current_page_rank[current_page_rank["id"] == current_id].iloc[0]["rank"]) # return the difference between the rank of the current_id and the new_page_rank 
  
  return [float(new_page_rank), float(absolute_difference)] # return an array with both values 

In [ ]:
count = 0
stable = False
while count < max_iterations and stable == False: # stop when the conditions are not fulfilled
  stable = True 
  udf_new_pagerank = udf(lambda l, i: new_pagerank(l,i,PageRankPDF), ArrayType(FloatType())) # create a udf for executing the new_pagerank function 
  id_rankDF = ReverseDF.select('id',udf_new_pagerank('links','id').alias('rank'))                              # store the array value that our function new_pagerank returns in id_rankDF
  NewPageRankDF = id_rankDF.select('id',id_rankDF.rank[0].alias('rank'),id_rankDF.rank[1].alias('difference')) # create a new spark dataframe with 3 columns: id, rank, and the difference value. 
  
  PageRankPDF = NewPageRankDF.toPandas() # convert to pandas
  
  for i in PageRankPDF["difference"]: # check if is stable or not with the difference values
    if i >= threshold: # check if the difference value is greater that the threshold
      stable = False # If yes, recalculate and pass to the next step, our PageRankPDF is not stable
                   
  count += 1
  print("Step:",count) # print the iteration where we are

Step: 1
Step: 2
Step: 3
Step: 4
Step: 5


In [ ]:
FinalPageRankPDF = PageRankPDF.filter(["id","rank"]).copy()
display(FinalPageRankPDF)        

id rank 266204 1.7034188E-5 925736 1.7034188E-5 155550 1.6930022E-5 277672 1.6930022E-5 27116818 1.6930022E-5 56120 1.6930022E-5 2526498 1.6930022E-5 8418 1.6930022E-5 152256 1.6930022E-5 7930 1.6930022E-5 305976 1.6930022E-5 14120158 1.6930022E-5 5314808 1.6930022E-5 65880 1.6930022E-5 679052 1.6930022E-5 116022 1.6930022E-5 35502 1.6930022E-5 4635146 1.6930022E-5 1452898 1.6930022E-5 3782000 1.6930022E-5 895968 1.7165932E-5 404186 1.6930022E-5 52826 1.6930022E-5 947696 1.6930022E-5 22936 1.6930022E-5 6466 1.6930022E-5 57706 1.6930022E-5 65758 1.6930022E-5 39412100 1.6930022E-5 31232 1.6930022E-5 2319464 1.6930022E-5 732244 1.6930022E-5 16277728 1.6930022E-5 447008 1.6930022E-5 427976 1.6930022E-5 200446 1.6930022E-5 171166 1.6930022E-5 99430 1.6930022E-5 178364 1.6930022E-5 2347646 1.6930022E-5 363804 1.6930022E-5 14494576 1.6930022E-5 8093724 1.6930022E-5 47489232 1.6930022E-5 29432500 1.6930022E-5 38508080 1.6930022E-5 37300890 1.6930022E-5 31321182 1.6930022E-5 19870750 1.6930022E-5 8916248 1.6930022E-5 237168 1.6930022E-5 292800 1.6930022E-5 346358 1.6930022E-5 32378800 1.6930022E-5 24630214 1.6930022E-5 47946 1.6930022E-5 45529058 1.6930022E-5 536678 1.8329334E-5 315858 1.6930022E-5 564006 1.6930022E-5 2165866 1.6930022E-5 22393832 1.6930022E-5 400892 1.6930022E-5 1571482 1.6930022E-5 6799304 1.6930022E-5 219112 1.6930022E-5 99308 1.6930022E-5 372466 1.6930022E-5 3639017 1.6930022E-5 11123595 1.6930022E-5 17599355 1.6930022E-5 1218903 1.6930022E-5 254127 1.6930022E-5 838629 1.6930022E-5 19008577 1.6930022E-5 5247 1.6930022E-5 1059205 1.6930022E-5 75275 1.6930022E-5 5040309 1.6930022E-5 194347 1.6930022E-5 297071 1.6930022E-5 3418807 1.6930022E-5 27995707 1.7165932E-5 2339717 1.6930022E-5 27283349 1.6930022E-5 55633 1.6930022E-5 12764007 1.6930022E-5 1071161 1.6930022E-5 38261031 1.6930022E-5 21107953 1.6930022E-5 39614987 1.6930022E-5 3228365 1.6930022E-5 1171445 1.6930022E-5 22133851 1.6930022E-5 5735 1.6930022E-5 25352943 1.6930022E-5 29830709 1.6930022E-5 3017183 1.6930022E-5 172997 1.6930022E-5 11124449 1.6930022E-5 107361 1.6930022E-5 22699565 1.6930022E-5 18456527 1.6930022E-5 467627 1.6930022E-5 84303 1.6930022E-5 31140501 1.6930022E-5 12137537 1.6930022E-5 90525 1.6930022E-5 358925 1.6930022E-5 1078115 1.6930022E-5 5955309 1.6930022E-5 345505 1.6930022E-5 1338951 1.6930022E-5 592311 1.6930022E-5 440055 1.6930022E-5 2111211 1.6930022E-5 502519 1.6930022E-5 22205 1.6930022E-5 82595 1.6930022E-5 60635 1.6930022E-5 47192285 1.6930022E-5 34900419 1.6930022E-5 61489 1.6930022E-5 45001409 1.6930022E-5 10656945 1.6930022E-5 981125 1.6930022E-5 19859405 1.6930022E-5 25913533 1.6930022E-5 23805739 1.6930022E-5 446887 1.6930022E-5 32207879 1.6930022E-5 248760 1.7034188E-5 105776 1.7034188E-5 2943008 1.6981974E-5 27424748 1.6981974E-5 765430 1.6930022E-5 28916 1.6930022E-5 101628 1.6930022E-5 5316396 1.6930022E-5 1099588 1.6930022E-5 316348 1.6930022E-5 893408 1.6930022E-5 1561236 1.6930022E-5 3988792 1.6930022E-5 50510 1.6930022E-5 9640 1.6930022E-5 28292412 1.6930022E-5 14194092 1.6930022E-5 519600 1.6930022E-5 143230 1.6930022E-5 8520848 1.6930022E-5 14119062 1.6930022E-5 14722840 1.6930022E-5 26997138 1.6930022E-5 288166 1.6930022E-5 87110 1.6930022E-5 294510 1.6930022E-5 435298 1.6930022E-5 31600 1.6930022E-5 4371506 1.6930022E-5 6823096 1.6930022E-5 651116 1.7165932E-5 1773394 1.6930022E-5 3360126 1.6930022E-5 13997672 1.6930022E-5 1283442 1.6930022E-5 126516 1.6930022E-5 196788 1.6930022E-5 12476210 1.6930022E-5 34269192 1.6930022E-5 653312 1.6930022E-5 990886 1.6930022E-5 31914470 1.6930022E-5 35299360 1.6930022E-5 6021678 1.6930022E-5 12189998 1.6930022E-5 4440558 1.6930022E-5 149330 1.6930022E-5 8537074 1.6930022E-5 10128 1.6930022E-5 62466 1.6930022E-5 4913064 1.6930022E-5 6773076 1.6930022E-5 32332 1.6930022E-5 33430 1.6930022E-5 330988 1.6930022E-5 16716 1.6930022E-5 19888 1.6930022E-5 211794 1.6930022E-5 26119592 1.6930022E-5 14175914 1.6930022E-5 1794256 1.6930022E-5 7271934 1.6930022E-5 11040148 1.6930022E-5

# Conclusions

PageRank is an algorithm used to determine the importance of a webpage in a network of interconnected webpages. It works by assigning a score, or "rank," to each webpage based on the number and importance of the webpages that link to it. 

The higher the PageRank, the higher the webpage will appear in search engine results. PageRank is one of the factors that Google uses to determine the relevance and credibility of a webpage, and it is an important part of the algorithm that helps to deliver relevant and useful search results to users.

The PageRank algorithm is based on the concept of "random surfer" and is calculated using the following formula: 

<img src="https://blogger3cero.com/wp-content/uploads/2019/05/formula-1024x263.jpg" />

where d is a damping factor, PR(A) is the PageRank of a webpage A, PR(i) is the PageRank of a webpage i, and C(i) is the number of outbound links on webpage i.

The most relevant function from this notebook, in our opinion, is *parse_links* function, which from a set of text returns all the filtered links taking into account its possible formats and the words that cannot be followed by links to other pages. 

In this work, we have learned how to implement PageRank algorithm in Spark, which is a powerful tool for big data processing. Spark allows us to distribute the computation of PageRank algorithm over a cluster of computers, making it possible to process large datasets efficiently.

It has been surprising to discover that from the Spark dataframe, python functions can't be called unless we define a User Defined Function. Also, we have made some research on the differences between broadcast and cache. We have used both of them to boost the performance in Spark. With both functions data is more available from quick and efficient processing. On the contrary, broadcast means to supply a copy of the data to every executor and cache will stop the processed data along with its required steps to compute that data. So, when we want to reduce communication costs of data we will use broadcast and when we want to reduce computation costs for repeated operations, we will use cache. 

Personally, learning about PageRank algorithm and how it works has been an interesting experience. It is fascinating to see how a simple algorithm can have such a significant impact on the way we interact with the Internet. The ability to analyze and process large datasets using Spark has also been very intriguing. Overall, this work has broadened our understanding of the technology behind search engines and the importance of data processing in modern applications.